In [8]:
import os
import cv2
import numpy as np
import pandas as pd

import matplotlib.pyplot as plt



In [9]:
def opticalFlowDense(image_current, image_next):
    """
    input: image_current, image_next (RGB images)
    calculates optical flow magnitude and angle and places it into HSV image
    * Set the saturation to the saturation value of image_next
    * Set the hue to the angles returned from computing the flow params
    * set the value to the magnitude returned from computing the flow params
    * Convert from HSV to RGB and return RGB image with same size as original image
    """
    gray_current = cv2.cvtColor(image_current, cv2.COLOR_RGB2GRAY)
    gray_next = cv2.cvtColor(image_next, cv2.COLOR_RGB2GRAY)
    
    hsv = np.zeros(image_current.shape)
    # set saturation
    hsv[:,:,1] = cv2.cvtColor(image_next, cv2.COLOR_RGB2HSV)[:,:,1]
 
    # Flow Parameters
    flow_mat = None
    image_scale = 0.5
    nb_images = 1
    win_size = 15
    nb_iterations = 2
    deg_expansion = 5
    STD = 1.3
    extra = 0

    # obtain dense optical flow paramters
    flow = cv2.calcOpticalFlowFarneback(gray_current, gray_next,  
                                        flow_mat, 
                                        image_scale, 
                                        nb_images, 
                                        win_size, 
                                        nb_iterations, 
                                        deg_expansion, 
                                        STD, 
                                        0)
                                        
        
    # convert from cartesian to polar
    mag, ang = cv2.cartToPolar(flow[..., 0], flow[..., 1])  
        
    # hue corresponds to direction
    hsv[:,:,0] = ang * (180/ np.pi / 2)
    
    # value corresponds to magnitude
    hsv[:,:,2] = cv2.normalize(mag,None,0,255,cv2.NORM_MINMAX)
    
    # convert HSV to float32's
    hsv = np.asarray(hsv, dtype= np.float32)    

    rgb_flow = cv2.cvtColor(hsv,cv2.COLOR_HSV2RGB)

    
    return rgb_flow


def crop_image(image, scale):
    """
    preprocesses the image
    
    input: image (480 (y), 640 (x), 3) RGB
    output: image (shape is (66, 220, 3) as RGB)
    
    This stuff is performed on my validation data and my training data
    Process: 
             1) Cropping out black spots
             3) resize to (66, 220, 3) if not done so already from perspective transform
    """
    # Crop out sky (top 130px) and the hood of the car (bottom 270px) 
    image_cropped = image[130:370,:] # -> (240, 640, 3)
    
    height = int(240*scale)
    width = int(640*scale)
    image = cv2.resize(image_cropped, (220, 66), interpolation = cv2.INTER_AREA)
    return image

def change_brightness(image, bright_factor):
    """
    Augments the brightness of the image by multiplying the saturation by a uniform random variable
    Input: image (RGB)
    returns: image with brightness augmentation
    """
    
    hsv_image = cv2.cvtColor(image, cv2.COLOR_RGB2HSV)
    # perform brightness augmentation only on the second channel
    hsv_image[:,:,2] = hsv_image[:,:,2] * bright_factor
    
    # change back to RGB
    image_rgb = cv2.cvtColor(hsv_image, cv2.COLOR_HSV2RGB)
    return image_rgb

def preprocess_image_from_path(image_path, scale_factor=0.5, bright_factor=1):
    img = cv2.imread(image_path)
    img = cv2.cvtColor(img, cv2.COLOR_BGR2RGB)
    img = change_brightness(img, bright_factor)
    img = crop_image(img, scale_factor)
    return img

def preprocess_image_valid_from_path(image_path, scale_factor=0.5):
    img = cv2.imread(image_path)
    img = cv2.cvtColor(img, cv2.COLOR_BGR2RGB)
    img = crop_image(img, scale_factor)
    return img

In [12]:
test_data = pd.read_csv('/srv/beegfs02/scratch/aegis_guardian/data/speed_prediction/deeps/valid_data.csv')
test_data = test_data[['image_path', 'time', 'speed']]

In [17]:
scale_factor = 0.5
for i in range(0, len(test_data)-1, 2):
    y1 = test_data.iloc[i]['speed']
    y2 = test_data.iloc[i+1]['speed']
    
    avg_speed =np.mean([y1,y2])
    
    x1 = preprocess_image_valid_from_path(test_data.iloc[i]['image_path'],scale_factor)
    x2 = preprocess_image_valid_from_path(test_data.iloc[i+1]['image_path'],scale_factor)

    i1 = test_data.iloc[i]['image_path']
    i2 = test_data.iloc[i+1]['image_path']
    
    rgb_diff = opticalFlowDense(x1, x2)
    rgb_diff = rgb_diff.reshape(1, rgb_diff.shape[0], rgb_diff.shape[1], rgb_diff.shape[2])

    print('----------------------------------------------------------------------------------------------------------------')
    print(f'Speed {i}: {y1}')
    print(f'Speed {i+1}: {y2}')
    print(f'Image {i}: {i1}')
    print(f'Image {i+1}: {i2}')
    print(f'RGB difference: {np.average(rgb_diff)}')
    print(f'Label: {avg_speed}')
    print('----------------------------------------------------------------------------------------------------------------')
    i+=2

----------------------------------------------------------------------------------------------------------------
Speed 0: 0.2923845878901177
Speed 1: 0.2915077567120695
Image 0: /srv/beegfs02/scratch/aegis_guardian/data/datasets/finetuning/training/Hammond/speed_pred/commaai-speed-challenge-master/data_train_preprocessed/3355.5833333349665.jpg
Image 1: /srv/beegfs02/scratch/aegis_guardian/data/datasets/finetuning/training/Hammond/speed_pred/commaai-speed-challenge-master/data_train_preprocessed/3355.6666666683.jpg
RGB difference: -317.4491882324219
Label: 0.2919461723010936
----------------------------------------------------------------------------------------------------------------
----------------------------------------------------------------------------------------------------------------
Speed 2: 0.4643621444679587
Speed 3: 0.4673321693336659
Image 2: /srv/beegfs02/scratch/aegis_guardian/data/datasets/finetuning/training/Hammond/speed_pred/commaai-speed-challenge-master/data_tr

----------------------------------------------------------------------------------------------------------------
Speed 24: 0.3314612138682246
Speed 25: 0.3321809822340051
Image 24: /srv/beegfs02/scratch/aegis_guardian/data/datasets/finetuning/training/Hammond/speed_pred/commaai-speed-challenge-master/data_train_preprocessed/900.7500000001302.jpg
Image 25: /srv/beegfs02/scratch/aegis_guardian/data/datasets/finetuning/training/Hammond/speed_pred/commaai-speed-challenge-master/data_train_preprocessed/900.8333333334635.jpg
RGB difference: -1735.53076171875
Label: 0.3318210980511148
----------------------------------------------------------------------------------------------------------------
----------------------------------------------------------------------------------------------------------------
Speed 26: 0.3579582862976325
Speed 27: 0.3579866234323933
Image 26: /srv/beegfs02/scratch/aegis_guardian/data/datasets/finetuning/training/Hammond/speed_pred/commaai-speed-challenge-master/

----------------------------------------------------------------------------------------------------------------
Speed 48: 0.311580733834076
Speed 49: 0.3133242647644958
Image 48: /srv/beegfs02/scratch/aegis_guardian/data/datasets/finetuning/training/Hammond/speed_pred/commaai-speed-challenge-master/data_train_preprocessed/2553.666666666841.jpg
Image 49: /srv/beegfs02/scratch/aegis_guardian/data/datasets/finetuning/training/Hammond/speed_pred/commaai-speed-challenge-master/data_train_preprocessed/2553.7500000001746.jpg
RGB difference: -1539.5313720703125
Label: 0.31245249929928587
----------------------------------------------------------------------------------------------------------------
----------------------------------------------------------------------------------------------------------------
Speed 50: 0.4352728927791735
Speed 51: 0.4354956555726698
Image 50: /srv/beegfs02/scratch/aegis_guardian/data/datasets/finetuning/training/Hammond/speed_pred/commaai-speed-challenge-mast

----------------------------------------------------------------------------------------------------------------
Speed 72: 0.3217364595038687
Speed 73: 0.3252358642183245
Image 72: /srv/beegfs02/scratch/aegis_guardian/data/datasets/finetuning/training/Hammond/speed_pred/commaai-speed-challenge-master/data_train_preprocessed/2369.083333333172.jpg
Image 73: /srv/beegfs02/scratch/aegis_guardian/data/datasets/finetuning/training/Hammond/speed_pred/commaai-speed-challenge-master/data_train_preprocessed/2369.1666666665055.jpg
RGB difference: -359.020751953125
Label: 0.3234861618610966
----------------------------------------------------------------------------------------------------------------
----------------------------------------------------------------------------------------------------------------
Speed 74: 0.3376957178012235
Speed 75: 0.3381679090948831
Image 74: /srv/beegfs02/scratch/aegis_guardian/data/datasets/finetuning/training/Hammond/speed_pred/commaai-speed-challenge-master

----------------------------------------------------------------------------------------------------------------
Speed 102: 0.5009955282869919
Speed 103: 0.5012446225015365
Image 102: /srv/beegfs02/scratch/aegis_guardian/data/datasets/finetuning/training/Hammond/speed_pred/commaai-speed-challenge-master/data_train_preprocessed/3865.583333335894.jpg
Image 103: /srv/beegfs02/scratch/aegis_guardian/data/datasets/finetuning/training/Hammond/speed_pred/commaai-speed-challenge-master/data_train_preprocessed/3865.6666666692277.jpg
RGB difference: -3386.1025390625
Label: 0.5011200753942642
----------------------------------------------------------------------------------------------------------------
----------------------------------------------------------------------------------------------------------------
Speed 104: 0.0005207398512171
Speed 105: 0.0
Image 104: /srv/beegfs02/scratch/aegis_guardian/data/datasets/finetuning/training/Hammond/speed_pred/commaai-speed-challenge-master/data_tra

...

----------------------------------------------------------------------------------------------------------------
Speed 20108: 0.5776699520942994
Speed 20109: 0.5780334491333002
Image 20108: /srv/beegfs02/scratch/aegis_guardian/data/datasets/finetuning/training/Hammond/speed_pred/commaai-speed-challenge-master/data_train_preprocessed/2205.333333332874.jpg
Image 20109: /srv/beegfs02/scratch/aegis_guardian/data/datasets/finetuning/training/Hammond/speed_pred/commaai-speed-challenge-master/data_train_preprocessed/2205.4166666662077.jpg
RGB difference: -220.4551239013672
Label: 0.5778517006137998
----------------------------------------------------------------------------------------------------------------
----------------------------------------------------------------------------------------------------------------
Speed 20110: 0.0
Speed 20111: 0.0
Image 20110: /srv/beegfs02/scratch/aegis_guardian/data/datasets/finetuning/training/Hammond/speed_pred/commaai-speed-challenge-master/data_tr

----------------------------------------------------------------------------------------------------------------
Speed 20134: 0.287400569314123
Speed 20135: 0.2878888577460406
Image 20134: /srv/beegfs02/scratch/aegis_guardian/data/datasets/finetuning/training/Hammond/speed_pred/commaai-speed-challenge-master/data_train_preprocessed/935.2500000001459.jpg
Image 20135: /srv/beegfs02/scratch/aegis_guardian/data/datasets/finetuning/training/Hammond/speed_pred/commaai-speed-challenge-master/data_train_preprocessed/935.3333333334792.jpg
RGB difference: -935.7128295898438
Label: 0.2876447135300818
----------------------------------------------------------------------------------------------------------------
----------------------------------------------------------------------------------------------------------------
Speed 20136: 0.5374821350051043
Speed 20137: 0.537198892228888
Image 20136: /srv/beegfs02/scratch/aegis_guardian/data/datasets/finetuning/training/Hammond/speed_pred/commaai-spe

----------------------------------------------------------------------------------------------------------------
Speed 20160: 0.2496109686825803
Speed 20161: 0.2512553453556156
Image 20160: /srv/beegfs02/scratch/aegis_guardian/data/datasets/finetuning/training/Hammond/speed_pred/commaai-speed-challenge-master/data_train_preprocessed/1399.916666666511.jpg
Image 20161: /srv/beegfs02/scratch/aegis_guardian/data/datasets/finetuning/training/Hammond/speed_pred/commaai-speed-challenge-master/data_train_preprocessed/1399.9999999998442.jpg
RGB difference: -1049.1524658203125
Label: 0.25043315701909796
----------------------------------------------------------------------------------------------------------------
----------------------------------------------------------------------------------------------------------------
Speed 20162: 0.199873511464711
Speed 20163: 0.2059418240166217
Image 20162: /srv/beegfs02/scratch/aegis_guardian/data/datasets/finetuning/training/Hammond/speed_pred/commaai

----------------------------------------------------------------------------------------------------------------
Speed 20184: 0.3118410909025454
Speed 20185: 0.310411248453929
Image 20184: /srv/beegfs02/scratch/aegis_guardian/data/datasets/finetuning/training/Hammond/speed_pred/commaai-speed-challenge-master/data_train_preprocessed/416.3333333333085.jpg
Image 20185: /srv/beegfs02/scratch/aegis_guardian/data/datasets/finetuning/training/Hammond/speed_pred/commaai-speed-challenge-master/data_train_preprocessed/416.4166666666418.jpg
RGB difference: -300.9619445800781
Label: 0.3111261696782372
----------------------------------------------------------------------------------------------------------------
----------------------------------------------------------------------------------------------------------------
Speed 20186: 0.3416746938072303
Speed 20187: 0.3415977052577985
Image 20186: /srv/beegfs02/scratch/aegis_guardian/data/datasets/finetuning/training/Hammond/speed_pred/commaai-sp

----------------------------------------------------------------------------------------------------------------
Speed 20210: 0.383489273288779
Speed 20211: 0.3834919475737293
Image 20210: /srv/beegfs02/scratch/aegis_guardian/data/datasets/finetuning/training/Hammond/speed_pred/commaai-speed-challenge-master/data_train_preprocessed/2570.833333333539.jpg
Image 20211: /srv/beegfs02/scratch/aegis_guardian/data/datasets/finetuning/training/Hammond/speed_pred/commaai-speed-challenge-master/data_train_preprocessed/2570.9166666668725.jpg
RGB difference: -107.20365142822266
Label: 0.38349061043125415
----------------------------------------------------------------------------------------------------------------
----------------------------------------------------------------------------------------------------------------
Speed 20212: 0.6385156432812448
Speed 20213: 0.6376740149502814
Image 20212: /srv/beegfs02/scratch/aegis_guardian/data/datasets/finetuning/training/Hammond/speed_pred/commaai